In [59]:
from urllib.parse import urlparse,urlencode
import urllib
import ipaddress
import re
import requests as rq
from bs4 import BeautifulSoup as bs 
import pandas as pd
import codecs
import csv

In [60]:
def has_Ip_address(url): #check if there is a ip_address in domain part
    domain_part=urlparse(url).netloc
    tem_s=domain_part.split(".")
    if(len(tem_s)!=4):
        return 0
    for x in tem_s:
        if(not x.isdigit()):
            return 0
        i=int(x)
        if(i<0 or i>255):
            return 0
    return 1

In [61]:
def gethtml(rooturl, encoding="utf-8"):
    # 默认解码方式utf-8
    try:
        resonse=rq.get(rooturl)
        resonse.encoding=encoding
        html=resonse.text
        return html
    except rq.exceptions.ConnectTimeout:
        pass
    except rq.exceptions.ConnectionError:
        pass
    

In [62]:
def Request_Url(url,html): #check if the url request more than 66% of total url in html 
    soup=bs(html,features="lxml")
    allnode_of_a=soup.find_all("a")
    allnode_of_img=soup.find_all("img")
    allnode_of_link=soup.find_all("link")
    allnode_of_script=soup.find_all("script")
    result1=[_.get("href") for _ in allnode_of_a]
    result2=[_.get("src") for _ in allnode_of_img]
    result3=[_.get("href") for _ in allnode_of_link]
    result4=[_.get("src") for _ in allnode_of_script]
    result=result1+result2+result3+result4
    urls=filter(result)
    different=0
    total=0
    domain_name=urllib.parse.urlparse(url).netloc
    for single_url in urls:
        single_domain_name=urllib.parse.urlparse(single_url).netloc
        if(single_domain_name!=domain_name):
            different+=1
        total+=1
    error_rate=(different/total)*100
    if(error_rate>66):
        return 1
    else:
        return 0

In [63]:
def filter(result):
    urlptn=r"https://(.+)"
    urls=[re.match(urlptn,str(_)) for _ in result]
    while None in urls:
        urls.remove(None)
    urls=[_.group() for _ in urls]
    return urls


In [64]:
def rdirect_page(response):
    if(response==""):
        return 1
    else:
        if(len(response.history)<2):
            return 0;
        else:
            return 1
    

In [65]:
def OnMouse_Change_Status_Bar(response):
    if(response==""):
        return 1
    else:
        if(re.findall("<script>.+onmouseover.+</script>", response.text)):
            return 1
        else:
            return 0

In [66]:
def right_click(response):
    if response=="":
        return 1
    else:
        if re.findall(r"event.button ?== ?2", response.text):
            return 1
        else:
            return 0

In [67]:
def Iframe(response):
    if response=="":
        return 1
    else:
        if re.findall(r"[<iframe>|<frameBorder>]",response.text):
            return 1
        else:
            return 0
    

In [68]:
def web_traffic(url):
  try:
    #Filling the whitespaces in the URL if any
    url = urllib.parse.quote(url)
    rank = bs(urllib.request.urlopen("http://data.alexa.com/data?cli=10&dat=s&url=" + url).read(), "xml").find(
        "REACH")['RANK']
    rank = int(rank)
  except TypeError:
        return 1
  if rank <100000:
    return 1
  else:
    return 0

In [69]:
def crawler(url,data):
    try:
        r = rq.get(url,headers=header,timeout=2.0)
        content = r.text
        soup = bs(content, 'html.parser')
        data["ip_address"]=has_Ip_address(url)
        data["Request_URL"]=Request_Url(url,content)
        data['redirect_page']=rdirect_page(r)
        data["Mouse_event"]=OnMouse_Change_Status_Bar(r)
        data["right_click"]=right_click(r)
        data["Iframe"]=Iframe(r)
        data["web_traffic"]=web_traffic(url)
        print(data)
    except Exception:
        pass
           
     
    
    

In [70]:
def load_raw_dataset(filename=None):
    f = codecs.open(filename, 'r', 'utf-8', errors='replace')
    lines = f.readlines()
    f.close()

    raw_dataset = []

    for line in lines:
        strs = line.strip().split('\t')
        label = strs[0]
        url = strs[1]
        data = {'url': url, 'label': label}
        raw_dataset.append(data)

    return raw_dataset

In [72]:
if __name__ == "__main__":
    header = {"User-Agent": "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) "
                            "Chrome/100.0.4896.75 Safari/537.36"}

    train_file = './train.txt'
    test_file ='./test.txt'

    train_dataset = load_raw_dataset(filename=train_file)
    test_dataset = load_raw_dataset(filename=test_file)
    i = 0
    j = 0
    with open ("train1.csv","w",newline="") as csvfile:
        writer=csv.writer(csvfile)
        header1=["url","label","ip_address","Request_url","redirect_page","Mouse_event","right_click","Iframe","web_traffic"]
        writer.writerow(header1)
        for train_data in train_dataset:
                train_url = train_data['url']
                crawler(url=train_url, data=train_data)
                try:
                    row=[train_url,train_data["label"],train_data["ip_address"],train_data["Request_URL"],train_data['redirect_page'],train_data['Mouse_event'],train_data['right_click'],
                        train_data['Iframe'],train_data['web_traffic']]
                    writer.writerow(row)
                except Exception:
                    pass
              
                print('train {num1}, {num2} left'.format(num1=i, num2=len(train_dataset) - i))
                i += 1
        csvfile.close()
            
   

    train_df = pd.DataFrame(train_dataset)
    train_output_path = 'train.csv'
    train_df.to_csv(train_output_path, sep=",", index=False, header=True)

    for test_data in test_dataset[0:10000]:
        test_url = test_data['url']
        crawler(url=test_url, data=test_data)
        
        print('test {num1}, {num2} left'.format(num1=j, num2=len(test_dataset) - j))
        j += 1

    test_df = pd.DataFrame(test_dataset)
    test_output_path = 'test.csv'
    test_df.to_csv(test_output_path, sep=",", index=False, header=True)

{'url': 'https://oregonstateparks.org/index.cfm?do=getinvolved.dsp_volunteeropp&oppid=847', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 1, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
train 0, 364199 left
train 1, 364198 left
train 2, 364197 left
{'url': 'http://michaelnielsen.org/blog/lecture-course-the-google-technology-stack/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
train 3, 364196 left
train 4, 364195 left
{'url': 'https://www.juventus.com/wps/portal/en/news/diritti%20di%20opzione%2022giugno2011/!ut/p/b1/vzpfbtsgfmafzq_qca7ygc7txhgdgpwh7nw-idj1m-luys6qrfbtj2htpsykdtoniyehvspvowcghwkxajtsfxlia-ko25-779ux3fgwft6vo76hpjtvokgaollcqoo0szftskbo0j4faimmmarrciq0xgv1gfkgof2d_77nspdfi6c2fxrkj3wmburwpns9drptl2egmypbqubxzxcsemi403sxnhlljarlsqxjjr0vebxajrhc2wnvriwxzmdd-s2c0ztnv4krqvt9cfhkwiclbhfeicup4g1mp_5ip_1u9vo1un09qsnkcdgsbxww2sat0o2

{'url': 'http://www.nbd.com.cn/articles/2019-01-31/1296829.html', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 54, 364145 left
{'url': 'https://www.website.com/en/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 55, 364144 left
train 56, 364143 left
train 57, 364142 left
train 58, 364141 left
{'url': 'https://www.rosewoodhotels.com/es/san-miguel-de-allende/about', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 1, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 59, 364140 left
{'url': 'http://www.csswinner.com/details/kith/12832', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
train 60, 364139 left
train 61, 364138 left
train 62, 3

train 115, 364084 left
{'url': 'https://www.backblaze.com/b2/cloud-storage.html?bznetid=9172655161550886000611', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 116, 364083 left
{'url': 'https://www.bike-components.de/fr/tiges/colliers-vis/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 117, 364082 left
train 118, 364081 left
train 119, 364080 left
train 120, 364079 left
{'url': 'https://visitsedona.com/events-calendar/members-summer-co-op-exhibition/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
train 121, 364078 left
train 122, 364077 left
train 123, 364076 left
train 124, 364075 left
train 125, 364074 left
train 126, 364073 left
train 127, 364072 left
{'url': 'https://www.monste

train 176, 364023 left
train 177, 364022 left
train 178, 364021 left
{'url': 'https://www.zkb.ch/de/uu/sp/umwelt-mobilitaet.html', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 179, 364020 left
{'url': 'http://www.orkutnavo.byethost11.com/', 'label': 'phishing', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
train 180, 364019 left
train 181, 364018 left
{'url': 'http://www.opb.org/news/article/5-things-to-know-about-the-proposal-to-repeal-oregons-clean-fuels-bill/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 182, 364017 left
{'url': 'http://www.theater-essen.de/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic':

{'url': 'http://www.utah.gov/treasurer/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 1, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 245, 363954 left
{'url': 'http://opentsdb.net/docs/3x/build/html/index.html', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
train 246, 363953 left
{'url': 'https://www.divessi.com/info/en-ic/scuba-diving/advanced-scuba-training/wreck-diving-172.html', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
train 247, 363952 left
train 248, 363951 left
train 249, 363950 left
train 250, 363949 left
train 251, 363948 left
{'url': 'https://thegrio.com/2012/04/03/burger-king-pulls-mary-j-blige-chicken-snack-wrap-commercial-from-youtube/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, '

...

{'url': 'https://www.constructiondive.com/news/gramercy-districts-8-acre-addition-to-open-a-year-ahead-of-development-sch/438040/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
train 50815, 313384 left
train 50816, 313383 left
train 50817, 313382 left
{'url': 'http://www.kutchina.com/js/detail.php', 'label': 'phishing', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
train 50818, 313381 left
{'url': 'https://www.tvnet.lv/term/557151/julijs-krumins', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 50819, 313380 left
train 50820, 313379 left
{'url': 'http://poetryproject.org/poets.html', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 1, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'we

{'url': 'http://www.bbbs.org/2016/10/help-big-dreaming-college/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
train 50890, 313309 left
{'url': 'https://jayisgames.com/review/recollect.php', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
train 50891, 313308 left
train 50892, 313307 left
train 50893, 313306 left
{'url': 'http://www.5ygs.com/~julienge/www.paypal.fr/webscrcmd=_login-done&login_access=1190737782.htm', 'label': 'phishing', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 50894, 313305 left
{'url': 'https://www.cfr.org/blog/outbreak-african-swine-flu-china-one-many?utm_source=feedburner&utm_medium=feed&utm_campaign=feed%3a+cfr_main+%28cfr.org+-+main+site+feed%29', 'label': 'legitimate', 'ip_address': 0,

{'url': 'https://cryptopay.me/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
train 50945, 313254 left
train 50946, 313253 left
{'url': 'https://www.muji.us/store/4549337086562.html', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 50947, 313252 left
train 50948, 313251 left
train 50949, 313250 left
train 50950, 313249 left
train 50951, 313248 left
train 50952, 313247 left
train 50953, 313246 left
{'url': 'https://www.openelement.com/app/newproject.fr.htm', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 50954, 313245 left
train 50955, 313244 left
train 50956, 313243 left
train 50957, 313242 left
{'url': 'https://www.bohemiancoding.com/awesome/', 'label': 'legitimate', 'ip_address': 0,

{'url': 'http://www.tica-poland.com/wp-content/plugins/fluid_forms/file-upload/server/php/files/online/TnpjM09ERXlNall6T1RNPQ==', 'label': 'phishing', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 51008, 313191 left
{'url': 'https://www.bluebeam.com/us/license/eula.asp', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 1, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 51009, 313190 left
train 51010, 313189 left
train 51011, 313188 left
{'url': 'https://www.maxim.com/maxim-man/why-do-women-like-assholes-2016-04', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
train 51012, 313187 left
train 51013, 313186 left
train 51014, 313185 left
train 51015, 313184 left
{'url': 'https://www.microsoftpressstore.com/store/windows-group-policy-resource-kit-windows-server-200

KeyboardInterrupt: 

test 0, 51510 left
test 1, 51509 left
{'url': 'https://eheadspace.org.au/headspace-centres/murray-bridge/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 2, 51508 left
test 3, 51507 left
{'url': 'https://hedgebrook.org/six-questions-for-hannah-lee-jones/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
test 4, 51506 left
test 5, 51505 left
{'url': 'http://www.commerce.wa.gov.au/announcements/new-regulations-improve-safe-use-combustible-cladding', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
test 6, 51504 left
{'url': 'http://www.ggj.gov.cn/gzdt/ggjgzdt/cwgl/cwglzwgk/cwgltzgg/201502/t20150202_11429.htm', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_ev

{'url': 'https://www.bleedingcool.com/2018/03/21/valiant-entertainment-june-2018-solicits/bss_010_variant-icon_jung-gi/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 1, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 62, 51448 left
{'url': 'https://usb.org/document-library/hid-descriptor-tool', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
test 63, 51447 left
test 64, 51446 left
test 65, 51445 left
{'url': 'https://revolt.tv/stories/2018/02/24/spotify-instagram-launch-interactive-black-girl-magic-playlist-highlighting-women-color-07003c8029', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 66, 51444 left
test 67, 51443 left
{'url': 'https://icom.museum/en/committee/ethics-committee/', 'label': 'legitimate', 'ip_address': 0, 'Request_U

{'url': 'https://www.microstrategy.com/us/resources/blog/tag?tagname=enterprise+reporting&groupid=2', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 130, 51380 left
{'url': 'https://www.naturallycurly.com/curlreading/ingredients?page=2', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 131, 51379 left
test 132, 51378 left
test 133, 51377 left
test 134, 51376 left
test 135, 51375 left
test 136, 51374 left
{'url': 'https://www.rodeohouston.com/tickets/carnival-rides-games-food', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 1, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
test 137, 51373 left
test 138, 51372 left
{'url': 'http://www.fhi.no/artikler?id=72828', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'M

{'url': 'http://www.realnames.com/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
test 206, 51304 left
test 207, 51303 left
test 208, 51302 left
{'url': 'https://www.weser-kurier.de/bremen/bremen-stadt_artikel,-zwei-neue-geschaefte-an-der-bischofsnadel-_arid,1805360.html', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 1, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 209, 51301 left
{'url': 'https://daneden.me/2018/01/05/subatomic-design-systems/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 1, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
test 210, 51300 left
{'url': 'https://urandom.ca/orbit-python/oldsite/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 211, 51299 left
test 212,

{'url': 'https://artdealers.org/gallery/pace-prints-pace-primitive', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
test 273, 51237 left
test 274, 51236 left
{'url': 'https://www.maxcdn.com/one/tutorial/cdn-slowness-bad-performance/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 275, 51235 left
test 276, 51234 left
test 277, 51233 left
{'url': 'http://planeg.com/wise/files/', 'label': 'phishing', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 278, 51232 left
test 279, 51231 left
{'url': 'https://xebialabs.com/technology/automic/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
test 280, 51230 left
{'url': 'http:

...

{'url': 'https://deathpenaltyinfo.org/list-defendants-mental-retardation-executed-united-states?did=1858', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
test 9791, 41719 left
test 9792, 41718 left
test 9793, 41717 left
{'url': 'http://www.thinkstockphotos.fr/image/photo-d%c3%a9veloppement-des-entreprises-%c3%a0-succ%c3%a8s-et-le-concept/905948482', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 1, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 9794, 41716 left
{'url': 'http://www.nbc29.com/story/39605269/fields-trial-day-10', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 1, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
test 9795, 41715 left
test 9796, 41714 left
test 9797, 41713 left
test 9798, 41712 left
test 9799, 41711 left
test 9800, 41710 left
test 9801, 41709 left
{'url': 'https://

test 9847, 41663 left
{'url': 'https://www.barclaycard.co.uk/business/help-and-support/card-machine/foreign-exchange-rates', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 9848, 41662 left
test 9849, 41661 left
test 9850, 41660 left
{'url': 'http://autocalc.no/language/en-GB/come1.html', 'label': 'phishing', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 9851, 41659 left
{'url': 'http://www.hydroflask.com/products/hydro-flask-insulated-water-bottle-32oz-large', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 1, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 9852, 41658 left
{'url': 'https://www.seattleaquarium.org/press-room?page=1', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe':

{'url': 'http://www.glos.ac.uk/courses/postgraduate/gde/pages/mdes-graphic-design-master-of-design.aspx', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 1, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 9894, 41616 left
test 9895, 41615 left
{'url': 'https://www.pay.nl/features/responsive-multilanguage-betaalscherm', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 9896, 41614 left
{'url': 'http://www.defence.gov.au/medals/imperial/badges/general-service-badge.asp', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 0, 'redirect_page': 1, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 9897, 41613 left
test 9898, 41612 left
{'url': 'https://www.cellcontrol.com/fleet-blog/exceeding-7-digits-the-financial-case-for-eliminating-distracted-driving', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redi

{'url': 'https://koyresort.com/products/malibu-cover-up-dress', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
test 9942, 41568 left
test 9943, 41567 left
test 9944, 41566 left
test 9945, 41565 left
{'url': 'http://www.paypol.byethost3.com/webscr.html?cmd=_login-run&dispatch=5885d80a13c0db1f998ca054efbdf2c29878a435fe324eec2511727fbf3e9efcad7d7d0f4fc38b541cde1631d0e3f9a2ad7d7d0f4fc38b541cde1631d0e3f9a2', 'label': 'phishing', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
test 9946, 41564 left
{'url': 'https://www.bol.com/nl/p/wolk-grand-canyon-bij-zonsopgang-glas-120x80-cm-foto-print-op-glas/9200000086018632/', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 1}
test 9947, 41563 left
{'url': 'http://rrdtool.paracoda.com/b/co.

{'url': 'https://www.addresses.com/zip-codes-by-city/north-carolina/clinton', 'label': 'legitimate', 'ip_address': 0, 'Request_URL': 1, 'redirect_page': 0, 'Mouse_event': 0, 'right_click': 0, 'Iframe': 1, 'web_traffic': 0}
test 9997, 41513 left
test 9998, 41512 left
test 9999, 41511 left


In [78]:
  with open ("test1.csv","w",newline="") as csvfile:
        writer=csv.writer(csvfile)
        header1=["url","label","ip_address","Request_url","redirect_page","Mouse_event","right_click","Iframe","web_traffic"]
        writer.writerow(header1)
        for test_data in test_dataset[0:10000]:
                test_url = test_data['url']
                try:
                    row=[test_url,test_data["label"],test_data["ip_address"],test_data["Request_URL"],test_data['redirect_page'],test_data['Mouse_event'],test_data['right_click'],
                        test_data['Iframe'],test_data['web_traffic']]
                    writer.writerow(row)
                except Exception:
                    pass

              
        csvfile.close()